In [1]:
!cat data/TREC/trec05p-1/README.txt
!python3 --version

TREC 2005 Spam Track Public Corpus

Copyright 2005 Gordon V. Cormack and Thomas R. Lynam

    gvcormac@uwaterloo.ca
    trlynam@uwaterloo.ca

Includes material released to public pomain and material
used with permission.

Permission is granted for research use by registered
participants in TREC 2005 (trec.nist.gov).  "Research
use" means any bona fide scientific investigation
including, but not restricted to, the 2005 "Spam Track" 
tasks.

Permission is NOT granted to publish this corpus
or any material portion (including file names and
judgements).

It is our intention to make this corpus available
to non-participants, on request, at a future date.


----

INSTRUCTIONS

1. The compressed file may be uncompressed with gzip, Winzip,
   or any other utility that understands gzip format.

2. The compressed file will unpack to a folder named trec05p-1

3. There is one main corpus with four subsets:

   trec05p-1/full   -- the main corpus with 92,189 messages
   trec05p-1/ham25  -- subset o

In [2]:
import os
from html.parser import HTMLParser


class MyHTMLParser(HTMLParser):
    def __init__ (self):
        super(MyHTMLParser, self).__init__()
        self.current_email = ""
    def handle_starttag(self, tag, attrs):
        pass
    def handle_endtag(self, tag):
        pass
    def handle_data(self, data):
        self.current_email += data + " "
    def error(self, message):
        print('---------------')
        print('ERROR: ' + message)
        print('---------------')
        return

In [3]:
def filter_message_headers (encoded_message):
    new_encoded_message = []
    i = 0
    while i < len(encoded_message):
        sline = encoded_message[i].decode('latin-1')
        if '-----Original Message-----' in sline:
            while i < len(encoded_message) and len(encoded_message[i].decode('latin-1').strip()) != 0:
                i += 1
        if i < len(encoded_message):
            new_encoded_message.append(encoded_message[i])
        i += 1
        
    return new_encoded_message
            

In [4]:
def extract_metadata (encoded_message, corpus, collection):
    sender = ""
    content_type = ""
    boundary = None
    body_index = None
    split_indices = []
    
    for i, line in enumerate(encoded_message):
        sline = line.decode('latin-1')
        if str.encode("From: ") in line:
            sender = sline[6:].strip()
        if content_type == '' and str.encode("Content-Type: ") in line:
            content_type = sline[14:sline.find(';')]
        if 'boundary' in sline and sline.find('=') != -1:
            boundary = sline[sline.find('=')+1:][1:-2]
            continue
        if boundary and boundary in sline:
            split_indices.append(i)
        if not body_index and sline.strip() == "":
            body_index = i
    if len(split_indices) == 0:
        split_indices.append(body_index)
    split_indices.append(len(encoded_message)-1)
    return (sender, content_type, boundary, split_indices)

In [5]:
res_dir = open("./data/TREC/trec05p-1/full/index")
ans = [line.split(' ') for line in res_dir]
index_search = [[False for j in range(1000)] for i in range(308)]

for i in range(len(ans)):
    if ans[i][0] == 'spam':
        index_search[int(ans[i][1][8:11])][int(ans[i][1][12:])] = True


In [6]:
data_dir = './data/TREC/trec05p-1/data/'

sender_spam = []
sender_ham = []

body_spam = []
body_ham = []

dir_limit = 1

for corpus in sorted(os.listdir(data_dir)):
    file_limit = 100
    for collection in sorted(os.listdir(f"{data_dir}/{corpus}/")):
        fin = open(f"{data_dir}/{corpus}/{collection}", 'rb')
        encoded_message = filter_message_headers(fin.readlines())
        sender, content_type, boundary, split_indices = extract_metadata(encoded_message, corpus, collection)
        charset = "latin-1"
        body = ""
        
        if len(split_indices) > 2:
            for i in range(len(split_indices) - 1):
                x = split_indices[i]
                y = split_indices[i + 1]
                j = x + 1
                while j < y:
                    line = encoded_message[j].decode("latin-1").strip()
                    if len(line) == 0:
                        break
                    j += 1
                print("--- EMAIL: --- ", collection, corpus, index_search[int(corpus)][int(collection)])
                parser = MyHTMLParser()
                parser.feed(b"".join(encoded_message[j+1:y]).decode(charset))
                body = parser.current_email
        else:
            print("--- EMAIL: --- ", collection, corpus, index_search[int(corpus)][int(collection)])
            try:
                parser = MyHTMLParser()   
                parser.feed(b"".join(encoded_message[split_indices[0]:split_indices[1]]).decode(charset))
                body = parser.current_email
            except:
                body = ""
            
        fin.close()
        
        if index_search[int(corpus)][int(collection)]:
            sender_spam.append(sender)
            body_spam.append(body)
        else:
            sender_ham.append(sender)
            body_ham.append(body)

--- EMAIL: ---  000 000 False
--- EMAIL: ---  001 000 False
--- EMAIL: ---  002 000 False
--- EMAIL: ---  003 000 False
--- EMAIL: ---  004 000 False
--- EMAIL: ---  005 000 False
--- EMAIL: ---  006 000 False
--- EMAIL: ---  007 000 False
--- EMAIL: ---  008 000 False
--- EMAIL: ---  009 000 False
--- EMAIL: ---  010 000 False
--- EMAIL: ---  011 000 False
--- EMAIL: ---  012 000 False
--- EMAIL: ---  013 000 False
--- EMAIL: ---  014 000 False
--- EMAIL: ---  015 000 False
--- EMAIL: ---  016 000 False
--- EMAIL: ---  017 000 False
--- EMAIL: ---  018 000 False
--- EMAIL: ---  019 000 False
--- EMAIL: ---  020 000 False
--- EMAIL: ---  021 000 False
--- EMAIL: ---  022 000 False
--- EMAIL: ---  023 000 False
--- EMAIL: ---  024 000 False
--- EMAIL: ---  025 000 False
--- EMAIL: ---  026 000 False
--- EMAIL: ---  027 000 False
--- EMAIL: ---  028 000 False
--- EMAIL: ---  029 000 False
--- EMAIL: ---  030 000 False
--- EMAIL: ---  031 000 False
--- EMAIL: ---  032 000 False
--- EMAIL:

--- EMAIL: ---  213 000 True
--- EMAIL: ---  213 000 True
--- EMAIL: ---  214 000 True
--- EMAIL: ---  214 000 True
--- EMAIL: ---  215 000 True
--- EMAIL: ---  215 000 True
--- EMAIL: ---  216 000 True
--- EMAIL: ---  216 000 True
--- EMAIL: ---  217 000 True
--- EMAIL: ---  217 000 True
--- EMAIL: ---  218 000 True
--- EMAIL: ---  218 000 True
--- EMAIL: ---  219 000 True
--- EMAIL: ---  219 000 True
--- EMAIL: ---  220 000 True
--- EMAIL: ---  220 000 True
--- EMAIL: ---  221 000 True
--- EMAIL: ---  221 000 True
--- EMAIL: ---  221 000 True
--- EMAIL: ---  222 000 True
--- EMAIL: ---  222 000 True
--- EMAIL: ---  222 000 True
--- EMAIL: ---  223 000 True
--- EMAIL: ---  223 000 True
--- EMAIL: ---  223 000 True
--- EMAIL: ---  224 000 True
--- EMAIL: ---  224 000 True
--- EMAIL: ---  225 000 True
--- EMAIL: ---  225 000 True
--- EMAIL: ---  225 000 True
--- EMAIL: ---  226 000 True
--- EMAIL: ---  227 000 True
--- EMAIL: ---  228 000 True
--- EMAIL: ---  229 000 True
--- EMAIL: ---

--- EMAIL: ---  115 001 True
--- EMAIL: ---  116 001 True
--- EMAIL: ---  116 001 True
--- EMAIL: ---  116 001 True
--- EMAIL: ---  117 001 True
--- EMAIL: ---  117 001 True
--- EMAIL: ---  117 001 True
--- EMAIL: ---  117 001 True
--- EMAIL: ---  118 001 True
--- EMAIL: ---  118 001 True
--- EMAIL: ---  118 001 True
--- EMAIL: ---  118 001 True
--- EMAIL: ---  119 001 True
--- EMAIL: ---  119 001 True
--- EMAIL: ---  119 001 True
--- EMAIL: ---  119 001 True
--- EMAIL: ---  120 001 True
--- EMAIL: ---  120 001 True
--- EMAIL: ---  120 001 True
--- EMAIL: ---  120 001 True
--- EMAIL: ---  121 001 True
--- EMAIL: ---  121 001 True
--- EMAIL: ---  121 001 True
--- EMAIL: ---  121 001 True
--- EMAIL: ---  122 001 True
--- EMAIL: ---  122 001 True
--- EMAIL: ---  122 001 True
--- EMAIL: ---  122 001 True
--- EMAIL: ---  123 001 True
--- EMAIL: ---  123 001 True
--- EMAIL: ---  123 001 True
--- EMAIL: ---  123 001 True
--- EMAIL: ---  124 001 True
--- EMAIL: ---  124 001 True
--- EMAIL: ---

--- EMAIL: ---  277 001 True
--- EMAIL: ---  278 001 True
--- EMAIL: ---  278 001 True
--- EMAIL: ---  278 001 True
--- EMAIL: ---  279 001 True
--- EMAIL: ---  279 001 True
--- EMAIL: ---  279 001 True
--- EMAIL: ---  280 001 True
--- EMAIL: ---  280 001 True
--- EMAIL: ---  280 001 True
--- EMAIL: ---  281 001 True
--- EMAIL: ---  281 001 True
--- EMAIL: ---  281 001 True
--- EMAIL: ---  282 001 True
--- EMAIL: ---  282 001 True
--- EMAIL: ---  282 001 True
--- EMAIL: ---  283 001 True
--- EMAIL: ---  283 001 True
--- EMAIL: ---  283 001 True
--- EMAIL: ---  284 001 True
--- EMAIL: ---  284 001 True
--- EMAIL: ---  284 001 True
--- EMAIL: ---  285 001 True
--- EMAIL: ---  285 001 True
--- EMAIL: ---  285 001 True
--- EMAIL: ---  286 001 True
--- EMAIL: ---  286 001 True
--- EMAIL: ---  286 001 True
--- EMAIL: ---  287 001 True
--- EMAIL: ---  287 001 True
--- EMAIL: ---  287 001 True
--- EMAIL: ---  288 001 True
--- EMAIL: ---  288 001 True
--- EMAIL: ---  288 001 True
--- EMAIL: ---

--- EMAIL: ---  161 002 False
--- EMAIL: ---  161 002 False
--- EMAIL: ---  161 002 False
--- EMAIL: ---  162 002 True
--- EMAIL: ---  162 002 True
--- EMAIL: ---  163 002 True
--- EMAIL: ---  164 002 True
--- EMAIL: ---  165 002 True
--- EMAIL: ---  166 002 True
--- EMAIL: ---  166 002 True
--- EMAIL: ---  167 002 True
--- EMAIL: ---  167 002 True
--- EMAIL: ---  167 002 True
--- EMAIL: ---  168 002 True
--- EMAIL: ---  169 002 True
--- EMAIL: ---  169 002 True
--- EMAIL: ---  170 002 True
--- EMAIL: ---  170 002 True
--- EMAIL: ---  170 002 True
--- EMAIL: ---  171 002 True
--- EMAIL: ---  171 002 True
--- EMAIL: ---  171 002 True
--- EMAIL: ---  172 002 True
--- EMAIL: ---  172 002 True
--- EMAIL: ---  172 002 True
--- EMAIL: ---  173 002 True
--- EMAIL: ---  174 002 True
--- EMAIL: ---  174 002 True
--- EMAIL: ---  174 002 True
--- EMAIL: ---  175 002 True
--- EMAIL: ---  175 002 True
--- EMAIL: ---  175 002 True
--- EMAIL: ---  176 002 True
--- EMAIL: ---  176 002 True
--- EMAIL: 

...

--- EMAIL: ---  056 305 True
--- EMAIL: ---  056 305 True
--- EMAIL: ---  057 305 True
--- EMAIL: ---  058 305 True
--- EMAIL: ---  059 305 True
--- EMAIL: ---  060 305 True
--- EMAIL: ---  060 305 True
--- EMAIL: ---  061 305 True
--- EMAIL: ---  061 305 True
--- EMAIL: ---  062 305 True
--- EMAIL: ---  062 305 True
--- EMAIL: ---  063 305 True
--- EMAIL: ---  063 305 True
--- EMAIL: ---  064 305 True
--- EMAIL: ---  064 305 True
--- EMAIL: ---  064 305 True
--- EMAIL: ---  065 305 True
--- EMAIL: ---  066 305 True
--- EMAIL: ---  066 305 True
--- EMAIL: ---  067 305 True
--- EMAIL: ---  067 305 True
--- EMAIL: ---  067 305 True
--- EMAIL: ---  067 305 True
--- EMAIL: ---  068 305 True
--- EMAIL: ---  068 305 True
--- EMAIL: ---  068 305 True
--- EMAIL: ---  068 305 True
--- EMAIL: ---  069 305 True
--- EMAIL: ---  070 305 True
--- EMAIL: ---  071 305 True
--- EMAIL: ---  071 305 True
--- EMAIL: ---  071 305 True
--- EMAIL: ---  071 305 True
--- EMAIL: ---  072 305 True
--- EMAIL: ---

--- EMAIL: ---  198 305 True
--- EMAIL: ---  198 305 True
--- EMAIL: ---  198 305 True
--- EMAIL: ---  199 305 True
--- EMAIL: ---  199 305 True
--- EMAIL: ---  199 305 True
--- EMAIL: ---  200 305 True
--- EMAIL: ---  200 305 True
--- EMAIL: ---  200 305 True
--- EMAIL: ---  201 305 True
--- EMAIL: ---  201 305 True
--- EMAIL: ---  201 305 True
--- EMAIL: ---  202 305 True
--- EMAIL: ---  202 305 True
--- EMAIL: ---  202 305 True
--- EMAIL: ---  203 305 True
--- EMAIL: ---  203 305 True
--- EMAIL: ---  203 305 True
--- EMAIL: ---  204 305 True
--- EMAIL: ---  204 305 True
--- EMAIL: ---  204 305 True
--- EMAIL: ---  205 305 True
--- EMAIL: ---  205 305 True
--- EMAIL: ---  205 305 True
--- EMAIL: ---  206 305 True
--- EMAIL: ---  206 305 True
--- EMAIL: ---  206 305 True
--- EMAIL: ---  207 305 True
--- EMAIL: ---  207 305 True
--- EMAIL: ---  207 305 True
--- EMAIL: ---  208 305 True
--- EMAIL: ---  208 305 True
--- EMAIL: ---  208 305 True
--- EMAIL: ---  209 305 True
--- EMAIL: ---

--- EMAIL: ---  017 306 True
--- EMAIL: ---  017 306 True
--- EMAIL: ---  018 306 True
--- EMAIL: ---  018 306 True
--- EMAIL: ---  018 306 True
--- EMAIL: ---  018 306 True
--- EMAIL: ---  019 306 True
--- EMAIL: ---  020 306 True
--- EMAIL: ---  021 306 True
--- EMAIL: ---  022 306 True
--- EMAIL: ---  023 306 False
--- EMAIL: ---  024 306 True
--- EMAIL: ---  024 306 True
--- EMAIL: ---  025 306 True
--- EMAIL: ---  026 306 True
--- EMAIL: ---  027 306 True
--- EMAIL: ---  028 306 True
--- EMAIL: ---  029 306 False
--- EMAIL: ---  029 306 False
--- EMAIL: ---  029 306 False
--- EMAIL: ---  029 306 False
--- EMAIL: ---  030 306 True
--- EMAIL: ---  030 306 True
--- EMAIL: ---  030 306 True
--- EMAIL: ---  031 306 True
--- EMAIL: ---  031 306 True
--- EMAIL: ---  031 306 True
--- EMAIL: ---  032 306 False
--- EMAIL: ---  033 306 False
--- EMAIL: ---  034 306 True
--- EMAIL: ---  034 306 True
--- EMAIL: ---  034 306 True
--- EMAIL: ---  035 306 False
--- EMAIL: ---  036 306 False
--- E

--- EMAIL: ---  193 306 True
--- EMAIL: ---  194 306 True
--- EMAIL: ---  194 306 True
--- EMAIL: ---  194 306 True
--- EMAIL: ---  195 306 True
--- EMAIL: ---  195 306 True
--- EMAIL: ---  195 306 True
--- EMAIL: ---  196 306 True
--- EMAIL: ---  196 306 True
--- EMAIL: ---  196 306 True
--- EMAIL: ---  197 306 True
--- EMAIL: ---  197 306 True
--- EMAIL: ---  197 306 True
--- EMAIL: ---  198 306 True
--- EMAIL: ---  198 306 True
--- EMAIL: ---  198 306 True
--- EMAIL: ---  199 306 True
--- EMAIL: ---  199 306 True
--- EMAIL: ---  199 306 True
--- EMAIL: ---  200 306 True
--- EMAIL: ---  200 306 True
--- EMAIL: ---  200 306 True
--- EMAIL: ---  201 306 True
--- EMAIL: ---  201 306 True
--- EMAIL: ---  201 306 True
--- EMAIL: ---  202 306 True
--- EMAIL: ---  202 306 True
--- EMAIL: ---  202 306 True
--- EMAIL: ---  203 306 False
--- EMAIL: ---  204 306 True
--- EMAIL: ---  204 306 True
--- EMAIL: ---  204 306 True
--- EMAIL: ---  205 306 True
--- EMAIL: ---  205 306 True
--- EMAIL: --

--- EMAIL: ---  038 307 True
--- EMAIL: ---  038 307 True
--- EMAIL: ---  038 307 True
--- EMAIL: ---  039 307 True
--- EMAIL: ---  039 307 True
--- EMAIL: ---  039 307 True
--- EMAIL: ---  040 307 True
--- EMAIL: ---  040 307 True
--- EMAIL: ---  040 307 True
--- EMAIL: ---  041 307 True
--- EMAIL: ---  041 307 True
--- EMAIL: ---  041 307 True
--- EMAIL: ---  042 307 True
--- EMAIL: ---  042 307 True
--- EMAIL: ---  042 307 True
--- EMAIL: ---  043 307 True
--- EMAIL: ---  043 307 True
--- EMAIL: ---  043 307 True
--- EMAIL: ---  044 307 True
--- EMAIL: ---  044 307 True
--- EMAIL: ---  044 307 True
--- EMAIL: ---  045 307 True
--- EMAIL: ---  045 307 True
--- EMAIL: ---  045 307 True
--- EMAIL: ---  046 307 True
--- EMAIL: ---  046 307 True
--- EMAIL: ---  046 307 True
--- EMAIL: ---  047 307 False
--- EMAIL: ---  048 307 False
--- EMAIL: ---  048 307 False
--- EMAIL: ---  048 307 False
--- EMAIL: ---  048 307 False
--- EMAIL: ---  049 307 False
--- EMAIL: ---  050 307 False
--- EMA

In [7]:
import collections
import string

all_ham = " ".join(body_ham)
all_spam = " ".join(body_spam)


collections.Counter(all_ham.translate(str.maketrans('', '', string.punctuation)).split(" ")).most_common(100)

[('', 6626158),
 ('the', 369316),
 ('to', 256056),
 ('and', 178152),
 ('of', 176012),
 ('a', 142931),
 ('in', 126732),
 ('\n', 106613),
 ('for', 95713),
 ('is', 88763),
 ('that', 76501),
 ('on', 75829),
 ('you', 59807),
 ('be', 58012),
 ('with', 53848),
 ('this', 52637),
 ('will', 48794),
 ('have', 47876),
 ('as', 44191),
 ('at', 43955),
 ('are', 43124),
 ('or', 42543),
 ('I', 41364),
 ('Enron', 41294),
 ('by', 38984),
 ('it', 36756),
 ('from', 36450),
 ('not', 36075),
 ('The', 30859),
 ('has', 30189),
 ('we', 29790),
 ('was', 28490),
 ('an', 27944),
 ('\n\n', 27704),
 ('your', 27559),
 ('its', 26846),
 ('said', 25264),
 ('would', 22679),
 ('any', 21358),
 ('if', 19417),
 ('but', 19179),
 ('our', 16900),
 ('been', 16659),
 ('me', 16180),
 ('about', 16040),
 ('he', 15897),
 ('all', 15878),
 ('which', 15510),
 ('can', 15427),
 ('more', 15075),
 ('company', 14852),
 ('up', 14465),
 ('they', 13973),
 ('email', 13650),
 ('may', 13119),
 ('their', 12909),
 ('Updated', 12690),
 ('out', 12681)

In [8]:
collections.Counter(all_spam.translate(str.maketrans('', '', string.punctuation)).split(" ")).most_common(100)

[('', 2197179),
 ('\n', 253480),
 ('the', 221236),
 ('of', 184656),
 ('and', 172823),
 ('to', 165861),
 ('in', 104745),
 ('a', 94527),
 ('is', 67098),
 ('this', 59121),
 ('for', 56547),
 ('you', 53425),
 ('or', 52058),
 ('that', 45465),
 ('be', 42297),
 ('are', 42233),
 ('with', 41778),
 ('as', 39445),
 ('on', 38322),
 ('your', 35498),
 ('from', 33410),
 ('not', 32381),
 ('statements', 27657),
 ('our', 27146),
 ('by', 24661),
 ('at', 24484),
 ('The', 24187),
 ('have', 22822),
 ('company', 20216),
 ('will', 20177),
 ('an', 19835),
 ('may', 19470),
 ('has', 17753),
 ('within', 17035),
 ('any', 16515),
 ('information', 15797),
 ('\n\n', 15173),
 ('I', 15093),
 ('This', 14770),
 ('it', 14448),
 ('can', 13945),
 ('its', 13936),
 ('report', 13200),
 ('which', 12469),
 ('we', 12322),
 ('email', 11878),
 ('all', 11652),
 ('investment', 10289),
 ('Inc', 9916),
 ('Act', 9911),
 ('such', 9736),
 ('You', 9616),
 ('these', 9404),
 ('only', 9374),
 ('\xa0', 9360),
 ('been', 9089),
 ('We', 8922),
 ('